In [615]:
import pandas as pd
import numpy as np

# MEMBACA DATA TRAINING

Langkah awal yang dilakukan adalah membaca data training. data inin berisi seluruh variabel yang dibutuhkan untuk melatih model

Proses pembacaan data dilakukan dengan menggunakan library pandas

In [616]:
#Untuk menampilkan 5 baris data set pertama
df = pd.read_excel('data_training.xlsx')
df.head()

FixedAcidity  VolatileAcidity  CitricAcid  ResidualSugar  Chlorides  \
0           7.3            0.740        0.08            1.7      0.094   
1           8.1            0.575        0.22            2.1      0.077   
2          10.1            0.430        0.40            2.6      0.092   
3          12.9            0.500        0.55            2.8      0.072   
4           8.4            0.360        0.32            2.2      0.081   

   FreeSulfurDioxide  TotalSulfurDioxide  Density    pH  Sulphates  Alcohol  \
0               10.0                45.0  0.99576  3.24       0.50      9.8   
1               12.0                65.0  0.99670  3.29       0.51      9.2   
2               13.0                52.0  0.99834  3.22       0.64     10.0   
3                7.0                24.0  1.00012  3.09       0.68     10.9   
4               32.0                79.0  0.99640  3.30       0.72     11.0   

   Quality    Id  
0        5  1366  
1        5   103  
2        7   942  
3        6   811  
4        6   918

# CLEANING DATA


1. Memeriksa data yang hilang atau tidak sesuai


Tahapan ini bertujuan untuk emmastikan kualitas data sebelum digunakan. Pada langkah ini akan dilihat data-data yang hilang atau tidak sesuai yang dapat memperngaruhi model.

In [617]:
import numpy as np
df.shape

# Replace "?"," ","N/A","Null", dan "Nan" menjadi NaN
df.replace(["?", " ", "N/A", "Null", "Nan", "0", 0], np.nan, inplace=True)

# Mengetahui banyaknya missing value pada masing-masing kolom
print(df.isnull().sum())



FixedAcidity           0
VolatileAcidity        0
CitricAcid            73
ResidualSugar          0
Chlorides              0
FreeSulfurDioxide      0
TotalSulfurDioxide     0
Density                0
pH                     0
Sulphates              0
Alcohol                0
Quality                0
Id                     1
dtype: int64


diperoleh bahwa kolom "CitricAcid" dan kolom "Id" memiliki kolom anomali. Kedua data tersebut nantinya akan dilakukan penanganan untuk diperbaiki.

2. Penanganan nilai 0 pada data (Menggunakan Mean)

Nilai 0 dalam dataset kadang tidak benar-benar menunjukkan nilai “nol sesungguhnya”, tetapi menandakan data yang hilang atau tidak terisi dengan benar. Tetapi terdapat pula kasus nilai 0 pada data yang memang benar-benar menunjukkan nilai "nol".

Untuk mengatasi hal ini, dilakukan langkah penggantian nilai 0 dengan nilai rata-rata (mean) dari kolom terkait. Tujuannya adalah agar distribusi data tetap seimbang dan tidak bias akibat adanya nilai ekstrem atau kosong.

In [618]:
# Kolom Citric Acid

#Menghitung rata-rata mean
avg_CitricAcid = df["CitricAcid"].astype("float").mean(axis=0)
print("Average of CitricAcid:", avg_CitricAcid)

#replace missing CitricAcid dengan mean
df["CitricAcid"].replace(np.nan, avg_CitricAcid, inplace=True)

Average of CitricAcid: 0.2922448979591837


/tmp/ipython-input-391531539.py:8: FutureWarning: A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values always behaves as a copy.

For example, when doing 'df[col].method(value, inplace=True)', try using 'df.method({col: value}, inplace=True)' or df[col] = df[col].method(value) instead, to perform the operation inplace on the original object.


  df["CitricAcid"].replace(np.nan, avg_CitricAcid, inplace=True)


3. Melakukan normalisasi

Normalisasi adalah proses menyelaraskan skala nilai pada setiap fitur (kolom) agar memiliki rentang yang sama. Tanpa normalisasi, fitur dengan skala besar dapat mendominasi fitur lain dengan skala kecil, sehingga hasil model menjadi tidak seimbang.

In [619]:
# Normalisasi kolom TotalSulfurDioxide
df["Id"] = (df["Id"] / df["Id"].max()).astype(float)

# cek hasil
print(df[["Id"]].head())


         Id
0  0.855354
1  0.064496
2  0.589856
3  0.507827
4  0.574828


In [620]:
# Normalisasi kolom TotalSulfurDioxide
df["TotalSulfurDioxide"] = (df["TotalSulfurDioxide"] / df["TotalSulfurDioxide"].max()).astype(float)

# cek hasil
print(df[["TotalSulfurDioxide"]].head())


   TotalSulfurDioxide
0            0.161871
1            0.233813
2            0.187050
3            0.086331
4            0.284173


In [621]:
# Normalisasi kolom FreeSulfurDioxide
df["FreeSulfurDioxide"] = (df["FreeSulfurDioxide"] / df["FreeSulfurDioxide"].max()).astype(float)

# cek hasil
print(df[["FreeSulfurDioxide"]].head())


   FreeSulfurDioxide
0           0.147059
1           0.176471
2           0.191176
3           0.102941
4           0.470588


4. Penanganan drop row

Langkah drop row dilakukan untuk menghapus baris data yang tidak valid, yaitu baris yang memiliki nilai kosong (missing value), nilai ekstrem (outlier), atau kesalahan input yang dapat mengganggu hasil analisis dan pelatihan model.

Tujuannya adalah agar data yang digunakan benar-benar bersih dan representatif terhadap kondisi sebenarnya.

In [622]:
#KOLOM Id
print("Jumlah data sebelum drop:", len(df))

# drop row yang punya NaN di kolom "Id"
df.dropna(subset=["Id"], axis=0, inplace=True)

# reset index biar rapi setelah row dihapus
df.reset_index(drop=True, inplace=True)

# cek jumlah data setelah drop
print("Jumlah data setelah drop:", len(df))

# cek apakah masih ada NaN
print("\nJumlah NaN di gId:")
print(df[["Id"]].isnull().sum())

# cek 5 baris awal
print("\n5 baris pertama:")
print(df.head())

# Cek 5 baris akhir
print("\n5 baris akhir:")
print(df.tail())

Jumlah data sebelum drop: 857
Jumlah data setelah drop: 856

Jumlah NaN di gId:
Id    0
dtype: int64

5 baris pertama:
   FixedAcidity  VolatileAcidity  CitricAcid  ResidualSugar  Chlorides  \
0           7.3            0.740        0.08            1.7      0.094   
1           8.1            0.575        0.22            2.1      0.077   
2          10.1            0.430        0.40            2.6      0.092   
3          12.9            0.500        0.55            2.8      0.072   
4           8.4            0.360        0.32            2.2      0.081   

   FreeSulfurDioxide  TotalSulfurDioxide  Density    pH  Sulphates  Alcohol  \
0           0.147059            0.161871  0.99576  3.24       0.50      9.8   
1           0.176471            0.233813  0.99670  3.29       0.51      9.2   
2           0.191176            0.187050  0.99834  3.22       0.64     10.0   
3           0.102941            0.086331  1.00012  3.09       0.68     10.9   
4           0.470588            0.284173 

4. Penanganan bilangan desimal

Penanganan bilangan desimal dilakukan untuk menyeragamkan format angka dalam dataset. Langkah ini dilakukan agar data mudah dibaca, konsisten, dan tidak menimbulkan kesalahan saat proses analisis maupun pelatihan model.

In [623]:
# Ubah semua nilai di kolom 'FixedAcidity' jadi desimal dengan 1 angka di belakang koma
df['FixedAcidity'] = df['FixedAcidity'].astype(float).round(1)

# Ubah semua nilai di kolom 'VolatileAcidity' jadi desimal dengan 2 angka di belakang koma
df['VolatileAcidity'] = df['VolatileAcidity'].astype(float).round(2)

# Ubah semua nilai di kolom 'CitricAcid' jadi desimal dengan 2 angka di belakang koma
df['CitricAcid'] = df['CitricAcid'].astype(float).round(2)

# Ubah semua nilai di kolom 'ResidualSugar' jadi desimal dengan 2 angka di belakang koma
df['ResidualSugar'] = df['ResidualSugar'].astype(float).round(2)

# Ubah semua nilai di kolom 'Chlorides' jadi desimal dengan 3 angka di belakang koma
df['Chlorides'] = df['Chlorides'].astype(float).round(3)

# Ubah semua nilai di kolom 'Density' jadi desimal dengan 3 angka di belakang koma
df['Density'] = df['Density'].astype(float).round(3)

# Ubah semua nilai di kolom 'pH' jadi desimal dengan 2 angka di belakang koma
df['pH'] = df['pH'].astype(float).round(2)

# Ubah semua nilai di kolom 'Sulphates' jadi desimal dengan 2 angka di belakang koma
df['Sulphates'] = df['Sulphates'].astype(float).round(2)

# Ubah semua nilai di kolom 'Alcohol' jadi desimal dengan 2 angka di belakang koma
df['Alcohol'] = df['Alcohol'].astype(float).round(1)

# Ubah semua nilai di kolom 'Id' jadi desimal dengan 2 angka di belakang koma
df['Id'] = df['Id'].astype(float).round(2)

# Ubah semua nilai di kolom 'TotalSulfurDioxide' jadi desimal dengan 2 angka di belakang koma
df['TotalSulfurDioxide'] = df['TotalSulfurDioxide'].astype(float).round(2)

# Ubah semua nilai di kolom 'FreeSulfurDioxide' jadi desimal dengan 2 angka di belakang koma
df['FreeSulfurDioxide'] = df['FreeSulfurDioxide'].astype(float).round(2)

# MEMBACA DATA BARU

Setelah data selesai melewati proses cleaning, selanjutnya data yang telah siap akan dibaca ulang. Adapun tujuan dari langkah ini adalah untuk memastikan bahwa hasil cleanign sudah tersimpan dengan baik dan juga menajdi titik awal untuk tahap pemodalan yang akan dilakukan.

In [624]:
df.to_csv('clean_df.csv', index=False)

In [625]:
import pandas
from pandas.plotting import scatter_matrix

import matplotlib.pyplot as plt
get_ipython().run_line_magic('matplotlib', 'inline')
from sklearn.tree import DecisionTreeClassifier

In [626]:
clean_df=pandas.read_csv('clean_df.csv')
clean_df

FixedAcidity  VolatileAcidity  CitricAcid  ResidualSugar  Chlorides  \
0             7.3             0.74        0.08            1.7      0.094   
1             8.1             0.57        0.22            2.1      0.077   
2            10.1             0.43        0.40            2.6      0.092   
3            12.9             0.50        0.55            2.8      0.072   
4             8.4             0.36        0.32            2.2      0.081   
..            ...              ...         ...            ...        ...   
851           6.7             1.04        0.08            2.3      0.067   
852           8.0             0.39        0.30            1.9      0.074   
853           7.4             0.35        0.33            2.4      0.068   
854           7.9             0.57        0.31            2.0      0.079   
855           7.5             0.52        0.40            2.2      0.060   

     FreeSulfurDioxide  TotalSulfurDioxide  Density    pH  Sulphates  Alcohol  \
0                 0.15                0.16    0.996  3.24       0.50      9.8   
1                 0.18                0.23    0.997  3.29       0.51      9.2   
2                 0.19                0.19    0.998  3.22       0.64     10.0   
3                 0.10                0.09    1.000  3.09       0.68     10.9   
4                 0.47                0.28    0.996  3.30       0.72     11.0   
..                 ...                 ...      ...   ...        ...      ...   
851               0.28                0.12    0.996  3.52       0.57     11.0   
852               0.47                0.30    0.997  3.39       0.61      9.0   
853               0.13                0.09    0.995  3.36       0.60     11.9   
854               0.15                0.28    0.997  3.29       0.69      9.5   
855               0.18                0.07    0.995  3.26       0.64     11.8   

     Quality    Id  
0          5  0.86  
1          5  0.06  
2          7  0.59  
3          6  0.51  
4          6  0.57  
..       ...   ...  
851        4  0.92  
852        5  0.96  
853        6  0.99  
854        6  0.76  
855        6  0.99  

[856 rows x 13 columns]

# MODEL DESSICION TREE

Algoritma Decision Tree merupakan salah satu metode supervised learning yang digunakan untuk melakukan klasifikasi. Metode ini bekerja dengan cara membentuk struktur pohon keputusan yang memecah data berdasarkan kondisi tertentu untuk memprediksi nilai target.

In [627]:
x=clean_df.drop('Quality',axis=1)
y=clean_df['Quality']

In [628]:
from sklearn.model_selection import train_test_split
x_train,x_test,y_train,y_test=train_test_split(x,y,test_size=0.2)

In [629]:
print(y.value_counts())

Quality
5    361
6    341
7    109
4     26
8     13
3      6
Name: count, dtype: int64


In [630]:
classifier=DecisionTreeClassifier()
classifier.fit(x_train,y_train)

DecisionTreeClassifier()

In [631]:
y_pret = classifier.predict(x_test)

In [632]:
from sklearn.metrics import classification_report, confusion_matrix, accuracy_score
dt_acc = accuracy_score(y_test, y_pret)
print(confusion_matrix(y_test, y_pret))
print(classification_report(y_test, y_pret))

[[ 0  1  0  0  0  0]
 [ 0  0  4  0  0  0]
 [ 3  3 53 19  3  0]
 [ 0  2 16 37  5  0]
 [ 0  0  5  5 12  0]
 [ 0  0  0  0  4  0]]
              precision    recall  f1-score   support

           3       0.00      0.00      0.00         1
           4       0.00      0.00      0.00         4
           5       0.68      0.65      0.67        81
           6       0.61      0.62      0.61        60
           7       0.50      0.55      0.52        22
           8       0.00      0.00      0.00         4

    accuracy                           0.59       172
   macro avg       0.30      0.30      0.30       172
weighted avg       0.60      0.59      0.59       172



/usr/local/lib/python3.12/dist-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
/usr/local/lib/python3.12/dist-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
/usr/local/lib/python3.12/dist-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))


In [633]:
df = pandas.DataFrame({'Actual': y_test, 'Predicted': y_pret})
df

Actual  Predicted
400       5          5
356       5          3
397       5          4
81        5          5
793       6          6
..      ...        ...
156       6          6
650       5          5
415       4          5
799       5          6
624       7          7

[172 rows x 2 columns]

In [634]:
x.columns = ['FixedAcidity', 'VolatileAcidity', 'CitricAcid', 'ResidualSugar', 'Chlorides',
              'FreeSulfurDioxide', 'TotalSulfurDioxide', 'Density', 'pH', 'Sulphates', 'Alcohol','Id']

y.columns = ['Quality']

# MODEL NAIVE BAYES CLASSIFIER

aive Bayes adalah algoritma klasifikasi berbasis teorema Bayes yang menggunakan pendekatan probabilistik. Metode ini mengasumsikan bahwa setiap fitur bersifat independen, meskipun dalam kenyataannya tidak selalu demikian. Model ini sering digunakan karena sederhana, cepat, dan efektif untuk data berukuran besar.

Meskipun sederhana, Naive Bayes mampu memberikan hasil yang cukup akurat dan efisien, terutama ketika fitur-fitur datanya tidak saling bergantung kuat.

In [635]:
from sklearn.naive_bayes import GaussianNB
from sklearn.metrics import classification_report, confusion_matrix, accuracy_score

# Inisialisasi model Naive Bayes
nb_model = GaussianNB()

# Training model
nb_model.fit(x_train, y_train)

# Prediksi
nb_pred = nb_model.predict(x_test)

# Evaluasi
nb_acc = accuracy_score(y_test, nb_pred)
print("=== Naive Bayes Classifier ===")
print("Akurasi :", nb_acc)
print("\nClassification Report:\n", classification_report(y_test, nb_pred))
print("\nConfusion Matrix:\n", confusion_matrix(y_test, nb_pred))

=== Naive Bayes Classifier ===
Akurasi : 0.5174418604651163

Classification Report:
               precision    recall  f1-score   support

           3       0.00      0.00      0.00         1
           4       0.33      0.25      0.29         4
           5       0.75      0.51      0.60        81
           6       0.43      0.60      0.50        60
           7       0.48      0.50      0.49        22
           8       0.00      0.00      0.00         4

    accuracy                           0.52       172
   macro avg       0.33      0.31      0.31       172
weighted avg       0.57      0.52      0.53       172


Confusion Matrix:
 [[ 0  0  0  1  0  0]
 [ 0  1  2  1  0  0]
 [ 0  1 41 35  3  1]
 [ 0  1 11 36  6  6]
 [ 0  0  1 10 11  0]
 [ 0  0  0  1  3  0]]


/usr/local/lib/python3.12/dist-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
/usr/local/lib/python3.12/dist-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
/usr/local/lib/python3.12/dist-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))


# MODEL KNN (K-NEAREST NEIGHNOR)

K-Nearest Neighbors (KNN) adalah algoritma klasifikasi berbasis jarak yang bekerja dengan cara membandingkan data baru terhadap data yang sudah ada. Ketika ada data baru yang akan diprediksi, KNN mencari sejumlah tetangga terdekat (nilai k) berdasarkan jarak.

Model ini tidak memerlukan proses pelatihan yang rumit, tetapi sensitif terhadap skala data, sehingga normalisasi sangat penting sebelum digunakan.

In [636]:
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
from sklearn.neighbors import KNeighborsClassifier
from sklearn.metrics import confusion_matrix, classification_report, accuracy_score

In [637]:
# Split data
X_train, X_test, y_train, y_test = train_test_split(x,y, test_size=0.2, random_state=42)

In [638]:
# Normalisasi
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)

In [639]:
# KNN
knn = KNeighborsClassifier(n_neighbors=5)
knn.fit(X_train_scaled, y_train)
knn_pred = knn.predict(X_test_scaled)

In [640]:
 #Evaluasi
y_pret = knn_pred
dp_acc = accuracy_score(y_test, y_pret)

print(confusion_matrix(y_test, y_pret))
print(classification_report(y_test, y_pret))

[[ 0  0  0  1  0  0]
 [ 0  0  3  3  0  0]
 [ 0  1 53 22  0  0]
 [ 0  0 24 36  4  0]
 [ 0  0  4 11  7  0]
 [ 0  0  1  2  0  0]]
              precision    recall  f1-score   support

           3       0.00      0.00      0.00         1
           4       0.00      0.00      0.00         6
           5       0.62      0.70      0.66        76
           6       0.48      0.56      0.52        64
           7       0.64      0.32      0.42        22
           8       0.00      0.00      0.00         3

    accuracy                           0.56       172
   macro avg       0.29      0.26      0.27       172
weighted avg       0.54      0.56      0.54       172



/usr/local/lib/python3.12/dist-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
/usr/local/lib/python3.12/dist-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
/usr/local/lib/python3.12/dist-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))


# PERBANDINGAN HASIL

Tahap ini dilakukan untuk melihat hasil akurasi terbaik dari ketiga model yang telah di lakukan.

In [641]:
print("=========================")
print("Perbandingan Akurasi Model")
print("=========================")
print("Decision Tree Accuracy:", dt_acc)
print("Naive Bayes Accuracy :", nb_acc)
print("KNN :", dp_acc)

Perbandingan Akurasi Model
Decision Tree Accuracy: 0.5930232558139535
Naive Bayes Accuracy : 0.5174418604651163
KNN : 0.5581395348837209


# MENENTUKAN MODEL TERBAIK

Pada tahap ini dilakukan proses untuk menentukan model terbaik berdasarkan hasil akurasi tertinggi, kemudian model tersebut digunakan untuk memprediksi data baru. Pertama, data baru (data tes) dibaca terlebih dahulu, lalu kolom Id lama diganti dengan Id baru, sedangkan kolom lainnya seperti fitur-fitur input tetap menggunakan data dari hasil training sebelumnya agar struktur datanya konsisten. Setelah itu, dilakukan proses prediksi terhadap kolom Quality menggunakan model terbaik yang telah dipilih. Hasil akhir berupa data yang sudah memiliki Id baru dan Quality hasil prediksi kemudian disimpan sebagai file baru yang siap digunakan lebih lanjut.

In [642]:
import numpy as np
import pandas as pd
from google.colab import files


# Baca data baru
data_baru = pd.read_csv("data_baru.csv", sep=';')
print("Banyaknya Data Baru :", data_baru.shape)

# Pilih model terbaik
accuracies = {'DecisionTree': dt_acc, 'NaiveBayes': nb_acc, 'KNN': dp_acc}
best_model_name = max(accuracies, key=accuracies.get)
model = {'DecisionTree': classifier, 'NaiveBayes': nb_model, 'KNN': knn}[best_model_name]
print("Model terbaik :", best_model_name)

# Ganti Id lama ke Id baru
predict_df = clean_df.copy()
if len(data_baru) != len(clean_df):
    (f"({len(data_baru)}), ({len(clean_df)})")
n = min(len(data_baru), len(clean_df))
predict_df = predict_df.iloc[:n].copy()
predict_df['Id'] = data_baru['Id'].iloc[:n].values

# Siapkan fitur (tanpa Id)
features = predict_df.drop(columns=['Id'], errors='ignore')
features = features.fillna(features.median(numeric_only=True)).fillna(0)

# Pastikan kolom fitur sesuai model training
try:
    required_cols = list(model.feature_names_in_)
    for col in required_cols:
        if col not in features.columns:
            features[col] = 0
    features = features[required_cols]
except:
    pass

# Terapkan scaler kalau digunakan saat training
try:
    features_scaled = scaler.transform(features)
except:
    features_scaled = features.values

# Prediksi nilai Quality
predicted = model.predict(features_scaled)
predicted = np.round(predicted).astype(int)
predicted = np.clip(predicted, 0, 10)

predict_df['Quality'] = predicted

print(predict_df.head())

Banyaknya Data Baru : (286, 2)
Model terbaik : DecisionTree
   FixedAcidity  VolatileAcidity  CitricAcid  ResidualSugar  Chlorides  \
0           7.3             0.74        0.08            1.7      0.094   
1           8.1             0.57        0.22            2.1      0.077   
2          10.1             0.43        0.40            2.6      0.092   
3          12.9             0.50        0.55            2.8      0.072   
4           8.4             0.36        0.32            2.2      0.081   

   FreeSulfurDioxide  TotalSulfurDioxide  Density    pH  Sulphates  Alcohol  \
0               0.15                0.16    0.996  3.24       0.50      9.8   
1               0.18                0.23    0.997  3.29       0.51      9.2   
2               0.19                0.19    0.998  3.22       0.64     10.0   
3               0.10                0.09    1.000  3.09       0.68     10.9   
4               0.47                0.28    0.996  3.30       0.72     11.0   

   Quality    Id  
0

/usr/local/lib/python3.12/dist-packages/sklearn/utils/validation.py:2739: UserWarning: X does not have valid feature names, but DecisionTreeClassifier was fitted with feature names
  warnings.warn(


In [643]:
# Simpan hasil RINGKAS
from google.colab import files

Prediksi_Quality_Terbaru = predict_df[['Id', 'Quality']].copy()

out_name_simple = "Prediksi_Quality_Terbaru.csv"
Prediksi_Quality_Terbaru.to_csv(out_name_simple, index=False)

print("\n File ringkas tersimpan sebagai:", out_name_simple)
print(Prediksi_Quality_Terbaru.head(20))



 File ringkas tersimpan sebagai: Prediksi_Quality_Terbaru.csv
      Id  Quality
0    222        3
1   1514        6
2    417        3
3    754        6
4    516        4
5   1120        4
6    180        6
7     82        6
8    632        6
9    592        5
10   501        5
11  1586        6
12  1096        5
13  1101        4
14  1488        6
15   700        3
16   631        5
17  1022        6
18  1420        6
19   882        6


In [644]:
# otomatis download
files.download(out_name_simple)

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

# GAMBAR PADA MODEL DESSICION TREE

Gambar pohon ini dibuat paling bawah dikarenakan agar dapat memudahkan dalam mengupload file code yang telah dibuat di github

In [645]:
from sklearn.tree import export_graphviz

feature_names = list(getattr(classifier, "feature_names_in_", x.columns))
class_names = list(map(str, getattr(classifier, "classes_", []))) or None

export_graphviz(classifier, out_file='tree.dot', feature_names=feature_names,
                class_names=class_names, rounded=True, proportion=False, precision=2, filled=True)


from subprocess import call
call(['dot', '-Tpng', 'tree.dot', '-o', 'tree.png', '-Gdpi=600'])

# Display in notebook
from IPython.display import Image
Image(filename='tree.png')